In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore')
import seaborn as sns
from pandas.io.json import json_normalize  

In [4]:
from google.colab import files
files.upload()

Saving dev.jsonl to dev.jsonl
Saving train.jsonl to train.jsonl


{'dev.jsonl': b'{"question": "does ethanol take more energy make that produces", "title": "Ethanol fuel", "answer": false, "passage": "All biomass goes through at least some of these steps: it needs to be grown, collected, dried, fermented, distilled, and burned. All of these steps require resources and an infrastructure. The total amount of energy input into the process compared to the energy released by burning the resulting ethanol fuel is known as the energy balance (or ``energy returned on energy invested\'\'). Figures compiled in a 2007 report by National Geographic Magazine point to modest results for corn ethanol produced in the US: one unit of fossil-fuel energy is required to create 1.3 energy units from the resulting ethanol. The energy balance for sugarcane ethanol produced in Brazil is more favorable, with one unit of fossil-fuel energy required to create 8 from the ethanol. Energy balance estimates are not easily produced, thus numerous such reports have been generated th

In [4]:
train=pd.read_json('train.jsonl',lines=True)
test=pd.read_json('dev.jsonl',lines=True)

In [5]:
train.head()

question  ...                                            passage
0    do iran and afghanistan speak the same language  ...  Persian (/ˈpɜːrʒən, -ʃən/), also known by its ...
1  do good samaritan laws protect those who help ...  ...  Good Samaritan laws offer legal protection to ...
2  is windows movie maker part of windows essentials  ...  Windows Movie Maker (formerly known as Windows...
3  is confectionary sugar the same as powdered sugar  ...  Powdered sugar, also called confectioners' sug...
4         is elder scrolls online the same as skyrim  ...  As with other games in The Elder Scrolls serie...

[5 rows x 4 columns]

In [6]:
test.head()

question  ...                                            passage
0   does ethanol take more energy make that produces  ...  All biomass goes through at least some of thes...
1             is house tax and property tax are same  ...  Property tax or 'house tax' is a local tax on ...
2  is pain experienced in a missing body part or ...  ...  Phantom pain sensations are described as perce...
3  is harry potter and the escape from gringotts ...  ...  Harry Potter and the Escape from Gringotts is ...
4  is there a difference between hydroxyzine hcl ...  ...  Hydroxyzine preparations require a doctor's pr...

[5 rows x 4 columns]

In [7]:
train=train.drop(labels='title', axis=1)
test=test.drop(labels='title', axis=1)

In [8]:
passages_train = []
questions_train = []


passages_test = []
questions_test = []



for item1,item2 in zip(train['passage'],train['question']):
   passages_train.append(item1)
   questions_train.append(item2)
   
 

for item1,item2 in zip(test['passage'],test['question']):
   passages_test.append(item1)
   questions_test.append(item2)
   
 

In [9]:
from transformers import DistilBertTokenizer, DistilBertForQuestionAnswering
import torch

In [10]:
tokenizer = DistilBertTokenizer.from_pretrained('distilbert-base-uncased',return_token_type_ids = True)
model = DistilBertForQuestionAnswering.from_pretrained('distilbert-base-uncased-distilled-squad')

In [ ]:
encoding = tokenizer.batch_encode_plus(passages_train,questions_train,padding=True,truncation=True,max_length=10,return_tensors='pt')
input_ids, attention_mask = encoding["input_ids"], encoding["attention_mask"]
start_scores, end_scores = model(input_ids, attention_mask=attention_mask)

In [ ]:
for index,(start_score,end_score,input_id) in enumerate(zip(start_scores,end_scores,input_ids)):
    max_startscore = torch.argmax(start_score)
    max_endscore = torch.argmax(end_score)
    ans_tokens = input_ids[index][max_startscore: max_endscore + 1]
    answer_tokens = tokenizer.convert_ids_to_tokens(ans_tokens, skip_special_tokens=True)
    answer_tokens_to_string = tokenizer.convert_tokens_to_string(answer_tokens)
    print ("\nQuestion: ",questions[index])
    print ("Answer: ", answer_tokens_to_string)

In [ ]:
### Session Crashed Multiple times so can not do prediction #######